<a target="_blank" href="https://colab.research.google.com/github/AI4Finance-Foundation/FinRL-Tutorials/blob/master/2-Advance/FinRL_Ensemble_StockTrading_ICAIF_2020.ipynb">
  <img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/>
</a>

# Deep Reinforcement Learning for Stock Trading from Scratch: Multiple Stock Trading Using Ensemble Strategy





# Content

* [1. Problem Definition](#0)
* [2. Getting Started - Load Python packages](#1)
    * [2.1. Install Packages](#1.1)    
    * [2.2. Check Additional Packages](#1.2)
    * [2.3. Import Packages](#1.3)
    * [2.4. Create Folders](#1.4)
* [3. Download Data](#2)
* [4. Preprocess Data](#3)        
    * [4.1. Technical Indicators](#3.1)
    * [4.2. Perform Feature Engineering](#3.2)
* [5.Build Environment](#4)  
    * [5.1. Training & Trade Data Split](#4.1)
    * [5.2. User-defined Environment](#4.2)   
    * [5.3. Initialize Environment](#4.3)    
* [6.Implement DRL Algorithms](#5)  
* [7.Backtesting Performance](#6)  
    * [7.1. BackTestStats](#6.1)
    * [7.2. BackTestPlot](#6.2)   
    * [7.3. Baseline Stats](#6.3)   
    * [7.3. Compare to Stock Market Index](#6.4)             

<a id='0'></a>
# Part 1. Problem Definition

This problem is to design an automated trading solution for single stock trading. We model the stock trading process as a Markov Decision Process (MDP). We then formulate our trading goal as a maximization problem.

The algorithm is trained using Deep Reinforcement Learning (DRL) algorithms and the components of the reinforcement learning environment are:


* Action: The action space describes the allowed actions that the agent interacts with the
environment. Normally, a ∈ A includes three actions: a ∈ {−1, 0, 1}, where −1, 0, 1 represent
selling, holding, and buying one stock. Also, an action can be carried upon multiple shares. We use
an action space {−k, ..., −1, 0, 1, ..., k}, where k denotes the number of shares. For example, "Buy
10 shares of AAPL" or "Sell 10 shares of AAPL" are 10 or −10, respectively

* Reward function: r(s, a, s′) is the incentive mechanism for an agent to learn a better action. The change of the portfolio value when action a is taken at state s and arriving at new state s',  i.e., r(s, a, s′) = v′ − v, where v′ and v represent the portfolio
values at state s′ and s, respectively

* State: The state space describes the observations that the agent receives from the environment. Just as a human trader needs to analyze various information before executing a trade, so
our trading agent observes many different features to better learn in an interactive environment.

* Environment: Dow 30 consituents


The data of the single stock that we will be using for this case study is obtained from Yahoo Finance API. The data contains Open-High-Low-Close price and volume.


<a id='0'></a>
# Part 2. Getting Started

<a id='1.1'></a>
## 2.1. Import Packages

In [5]:
import warnings
warnings.filterwarnings("ignore")

In [6]:
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
# matplotlib.use('Agg')
import datetime
import statistics 
from stable_baselines3.common.callbacks import BaseCallback

%matplotlib inline
from FinRL.finrl.meta.preprocessor.yahoodownloader import YahooDownloader
from FinRL.finrl.meta.preprocessor.preprocessors import FeatureEngineer, data_split
from FinRL.finrl.meta.env_stock_trading.env_stocktrading import StockTradingEnv
from FinRL.finrl.agents.stablebaselines3.models import DRLAgent,DRLEnsembleAgent
from FinRL.finrl.plot import backtest_stats, backtest_plot, get_daily_return, get_baseline
from stable_baselines3.common.vec_env import DummyVecEnv
from pprint import pprint

import sys
sys.path.append("../FinRL-Library")

import itertools

<a id='1.4'></a>
## 2.2. Create Folders

In [ ]:
import os
from FinRL.finrl.main import check_and_make_directories
from FinRL.finrl.config import (
    DATA_SAVE_DIR,
    TRAINED_MODEL_DIR,
    TENSORBOARD_LOG_DIR,
    RESULTS_DIR,
    INDICATORS,
)


check_and_make_directories([DATA_SAVE_DIR, TRAINED_MODEL_DIR, TENSORBOARD_LOG_DIR, RESULTS_DIR])

<a id='2'></a>
# Part 3. Download Data
Yahoo Finance is a website that provides stock data, financial news, financial reports, etc. All the data provided by Yahoo Finance is free.
* FinRL uses a class **YahooDownloader** to fetch data from Yahoo Finance API
* Call Limit: Using the Public API (without authentication), you are limited to 2,000 requests per hour per IP (or up to a total of 48,000 requests a day).




-----
class YahooDownloader:
    Provides methods for retrieving daily stock data from
    Yahoo Finance API

    Attributes
    ----------
        start_date : str
            start date of the data (modified from config.py)
        end_date : str
            end date of the data (modified from config.py)
        ticker_list : list
            a list of stock tickers (modified from config.py)

    Methods
    -------
    fetch_data()
        Fetches data from yahoo API


In [ ]:
# Data from 01/01/2009 to 09/30/2015 is used for training, and the
# data from 10/01/2015 to 12/31/2015 is used for validation
# and tuning of parameters. Finally, we test our agent’s
# performance on trading data, which is the unseen outof-sample data from
# 01/01/2016 to 05/08/2020.
# date format: '%Y-%m-%d'
TRAIN_START_DATE = '2009-01-01'
TRAIN_END_DATE = '2015-09-30'
TEST_START_DATE = '2015-09-30'
TEST_END_DATE = '2020-05-08'
#https://en.wikipedia.org/wiki/Dow_Jones_Industrial_Average
#March 19, 2015
DOW_30_TICKER = ["AAPL", "AXP", "BA", "CAT", "CSCO", "CVX", "DD", "DIS", "GE", "GS",
 "HD", "IBM", "INTC", "JNJ", "JPM", "KO", "MCD", "MMM", "MRK", "MSFT",
 "NKE", "PFE", "PG", "TRV", "UNH", "UTX", "V", "VZ", "WMT", "XOM"]


df = YahooDownloader(start_date = TRAIN_START_DATE,
                     end_date = TEST_END_DATE,
                     ticker_list = DOW_30_TICKER).fetch_data()

YF deprecation warning: set proxy via new config function: yf.set_config(proxy=proxy)


[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

Shape of DataFrame:  (82824, 8)


In [9]:
df.head()

Price        date      close       high        low       open     volume  \
0      2009-01-02   2.727417   2.736134   2.559415   2.581054  746015200   
1      2009-01-02  14.929296  15.076040  14.211021  14.342318   10955700   
2      2009-01-02  33.941090  34.173615  32.088393  32.103395    7010200   
3      2009-01-02  30.344687  30.389967  28.921571  29.050946    7117200   
4      2009-01-02  11.166079  11.192414  10.698631  10.803972   40980600   

Price   tic  day  
0      AAPL    4  
1       AXP    4  
2        BA    4  
3       CAT    4  
4      CSCO    4

In [10]:
df.tail()

Price        date       close        high         low        open    volume  \
82819  2020-05-07  264.821869  271.595741  264.375843  270.452816   3162300   
82820  2020-05-07  176.045212  178.222648  175.072113  175.110645   9262200   
82821  2020-05-07   41.660736   42.087987   41.360910   42.050507  14083100   
82822  2020-05-07   37.832596   38.481297   37.711545   38.319895  27345600   
82823  2020-05-07   34.580288   35.385389   34.369242   35.143075  22160300   

Price  tic  day  
82819  UNH    3  
82820    V    3  
82821   VZ    3  
82822  WMT    3  
82823  XOM    3

In [11]:
df.shape

(82824, 8)

In [12]:
df.sort_values(['date','tic']).head()

Price        date      close       high        low       open     volume  \
0      2009-01-02   2.727417   2.736134   2.559415   2.581054  746015200   
1      2009-01-02  14.929296  15.076040  14.211021  14.342318   10955700   
2      2009-01-02  33.941090  34.173615  32.088393  32.103395    7010200   
3      2009-01-02  30.344687  30.389967  28.921571  29.050946    7117200   
4      2009-01-02  11.166079  11.192414  10.698631  10.803972   40980600   

Price   tic  day  
0      AAPL    4  
1       AXP    4  
2        BA    4  
3       CAT    4  
4      CSCO    4

In [13]:
df.date.unique()[:126]
#3 month trading is 63 days, not 90.

array(['2009-01-02', '2009-01-05', '2009-01-06', '2009-01-07',
       '2009-01-08', '2009-01-09', '2009-01-12', '2009-01-13',
       '2009-01-14', '2009-01-15', '2009-01-16', '2009-01-20',
       '2009-01-21', '2009-01-22', '2009-01-23', '2009-01-26',
       '2009-01-27', '2009-01-28', '2009-01-29', '2009-01-30',
       '2009-02-02', '2009-02-03', '2009-02-04', '2009-02-05',
       '2009-02-06', '2009-02-09', '2009-02-10', '2009-02-11',
       '2009-02-12', '2009-02-13', '2009-02-17', '2009-02-18',
       '2009-02-19', '2009-02-20', '2009-02-23', '2009-02-24',
       '2009-02-25', '2009-02-26', '2009-02-27', '2009-03-02',
       '2009-03-03', '2009-03-04', '2009-03-05', '2009-03-06',
       '2009-03-09', '2009-03-10', '2009-03-11', '2009-03-12',
       '2009-03-13', '2009-03-16', '2009-03-17', '2009-03-18',
       '2009-03-19', '2009-03-20', '2009-03-23', '2009-03-24',
       '2009-03-25', '2009-03-26', '2009-03-27', '2009-03-30',
       '2009-03-31', '2009-04-01', '2009-04-02', '2009-

In [14]:
len(df.tic.unique())

29

In [15]:
df.tic.value_counts()

tic
AAPL    2856
AXP     2856
BA      2856
CAT     2856
CSCO    2856
CVX     2856
DD      2856
DIS     2856
GE      2856
GS      2856
HD      2856
IBM     2856
INTC    2856
JNJ     2856
JPM     2856
KO      2856
MCD     2856
MMM     2856
MRK     2856
MSFT    2856
NKE     2856
PFE     2856
PG      2856
TRV     2856
UNH     2856
V       2856
VZ      2856
WMT     2856
XOM     2856
Name: count, dtype: int64

# Part 4: Preprocess Data
Data preprocessing is a crucial step for training a high quality machine learning model. We need to check for missing data and do feature engineering in order to convert the data into a model-ready state.
* Add technical indicators. In practical trading, various information needs to be taken into account, for example the historical stock prices, current holding shares, technical indicators, etc. In this article, we demonstrate two trend-following technical indicators: MACD and RSI.
* Add turbulence index. Risk-aversion reflects whether an investor will choose to preserve the capital. It also influences one's trading strategy when facing different market volatility level. To control the risk in a worst-case scenario, such as financial crisis of 2007–2008, FinRL employs the financial turbulence index that measures extreme asset price fluctuation.

In [16]:
INDICATORS = ['macd',
               'rsi_30',
               'cci_30',
               'dx_30']

In [17]:
fe = FeatureEngineer(use_technical_indicator=True,
                     tech_indicator_list = INDICATORS,
                     use_turbulence=True,
                     user_defined_feature = False)

processed = fe.preprocess_data(df)
processed = processed.copy()
processed = processed.fillna(0)
processed = processed.replace(np.inf,0)

Successfully added technical indicators
Successfully added turbulence index


In [18]:
processed.sample(5)

date      close       high        low       open    volume   tic  \
50175  2015-11-16  60.955395  60.968728  58.515848  58.515848  10101100   CVX   
51750  2016-02-04  45.293911  45.386980  44.254633  44.254633  21651300   JPM   
58802  2017-01-23  56.840477  56.984925  56.488384  56.605750  23097600  MSFT   
59325  2017-02-16  50.719082  51.286729  50.547884  51.250691   8374200   NKE   
4227   2009-07-31  35.107361  35.891601  35.056766  35.543754  12663900    PG   

       day      macd     rsi_30      cci_30      dx_30  turbulence  
50175    0  0.928207  55.117226   18.139837  13.086190   29.886076  
51750    3 -1.015984  44.321043  -43.004349  26.786085   79.483498  
58802    0  0.225519  57.478030   30.537657   9.422978   34.059171  
59325    3  0.885237  61.903408  189.782189  44.176623   39.021721  
4227     4  0.721645  58.964392   98.673318   7.992102    0.000000

<a id='4'></a>
# Part 5. Design Environment
Considering the stochastic and interactive nature of the automated stock trading tasks, a financial task is modeled as a **Markov Decision Process (MDP)** problem. The training process involves observing stock price change, taking an action and reward's calculation to have the agent adjusting its strategy accordingly. By interacting with the environment, the trading agent will derive a trading strategy with the maximized rewards as time proceeds.

Our trading environments, based on OpenAI Gym framework, simulate live stock markets with real market data according to the principle of time-driven simulation.

The action space describes the allowed actions that the agent interacts with the environment. Normally, action a includes three actions: {-1, 0, 1}, where -1, 0, 1 represent selling, holding, and buying one share. Also, an action can be carried upon multiple shares. We use an action space {-k,…,-1, 0, 1, …, k}, where k denotes the number of shares to buy and -k denotes the number of shares to sell. For example, "Buy 10 shares of AAPL" or "Sell 10 shares of AAPL" are 10 or -10, respectively. The continuous action space needs to be normalized to [-1, 1], since the policy is defined on a Gaussian distribution, which needs to be normalized and symmetric.

In [19]:
stock_dimension = len(processed.tic.unique())
state_space = 1 + 2*stock_dimension + len(INDICATORS)*stock_dimension
print(f"Stock Dimension: {stock_dimension}, State Space: {state_space}")


Stock Dimension: 29, State Space: 175


In [ ]:
num_stock_shares = [0] * stock_dimension
ensemble_env_kwargs = {
        "hmax": 50000, 
        "initial_amount": 100000000,
        "buy_cost_pct": 0.0015,
        "sell_cost_pct": 0.0015,
        "state_space": state_space,
        "stock_dim": stock_dimension,
        "tech_indicator_list": INDICATORS,
        "action_space": stock_dimension,
        "reward_scaling": 1e-4,
        "print_verbosity": 10,
    }

# Create lists of cost percentages for each stock
buy_cost_list = [0.0015] * stock_dimension  # 0.15% transaction cost for each stock
sell_cost_list = [0.0015] * stock_dimension

# Update env_kwargs
env_kwargs = {
    "hmax": 50000, 
    "initial_amount": 100000000,
    "buy_cost_pct": buy_cost_list,     
    "sell_cost_pct": sell_cost_list,   
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": INDICATORS,
    "action_space": stock_dimension,
    "reward_scaling": 1e-4,
    "print_verbosity": 10,
    "num_stock_shares": [0] * stock_dimension
}

<a id='5'></a>
# Part 6: Implement DRL Algorithms
* The implementation of the DRL algorithms are based on **OpenAI Baselines** and **Stable Baselines**. Stable Baselines is a fork of OpenAI Baselines, with a major structural refactoring, and code cleanups.
* FinRL library includes fine-tuned standard DRL algorithms, such as DQN, DDPG,
Multi-Agent DDPG, PPO, SAC, A2C and TD3. We also allow users to
design their own DRL algorithms by adapting these DRL algorithms.

* In this notebook, we are training and validating 3 agents (A2C, PPO, DDPG) using Rolling-window Ensemble Method ([reference code](https://github.com/AI4Finance-LLC/Deep-Reinforcement-Learning-for-Automated-Stock-Trading-Ensemble-Strategy-ICAIF-2020/blob/80415db8fa7b2179df6bd7e81ce4fe8dbf913806/model/models.py#L92))

In [21]:
rebalance_window = 63 # rebalance_window is the number of days to retrain the model
validation_window = 63 # validation_window is the number of days to do validation and trading (e.g. if validation_window=63, then both validation and trading period will be 63 days)

ensemble_agent = DRLEnsembleAgent(df=processed,
                 train_period=(TRAIN_START_DATE,TRAIN_END_DATE),
                 val_test_period=(TEST_START_DATE,TEST_END_DATE),
                 rebalance_window=rebalance_window,
                 validation_window=validation_window,
                 **ensemble_env_kwargs)



In [22]:
VALIDATION_START_DAY = '2015-10-01'
VALIDATION_END_DAY = '2015-12-31'

TRADE_START_DAY = '2016-01-01'
TRADE_END_DAY = '2020-05-08'
train = data_split(processed, TRAIN_START_DATE,
                    VALIDATION_END_DAY)


trade = data_split(
    processed, TRADE_START_DAY , TRADE_END_DAY)

e_train_gym = StockTradingEnv(df=train, **env_kwargs)
env_train, _ = e_train_gym.get_sb_env()

agent = DRLAgent(env=env_train)

In [23]:

A2C_model_kwargs = {"n_steps": 5, "ent_coef": 0.01, "learning_rate": 0.0007}
PPO_model_kwargs = {
    "n_steps": 2048,
    "ent_coef": 0.01,
    "learning_rate": 0.00025,
    "batch_size": 64,
}
DDPG_model_kwargs = None

TD3_model_kwargs = None
SAC_model_kwargs = None
timesteps_dict = {'a2c' : 100_000,
                 'ppo' : 100_000,
                 'ddpg' : None
                 }

In [24]:

print("==============Model Training A2C ===========")

model_a2c = agent.get_model("a2c")
trained_a2c = agent.train_model(
    model=model_a2c, tb_log_name="a2c", total_timesteps=timesteps_dict['a2c']
)

==============Model Training A2C ===========
{'n_steps': 5, 'ent_coef': 0.01, 'learning_rate': 0.0007}
Using cpu device
--------------------------------------
| time/                 |            |
|    fps                | 61         |
|    iterations         | 100        |
|    time_elapsed       | 8          |
|    total_timesteps    | 500        |
| train/                |            |
|    entropy_loss       | -41.3      |
|    explained_variance | 0.000146   |
|    learning_rate      | 0.0007     |
|    n_updates          | 99         |
|    policy_loss        | 2.96e+03   |
|    reward             | 36.307095  |
|    reward_max         | 72.396095  |
|    reward_mean        | 25.217707  |
|    reward_min         | -49.807255 |
|    std                | 1          |
|    value_loss         | 5.39e+03   |
--------------------------------------
--------------------------------------
| time/                 |            |
|    fps                | 63         |
|    iterations       

In [27]:
# Calculate turbulence threshold from training data
train_turbulence = processed
turbulence_threshold = np.quantile(train_turbulence.turbulence.values, 0.99)


In [30]:
print("==============Start Trading A2C===========")
e_trade_gym = StockTradingEnv(
    df=trade, 
    turbulence_threshold=turbulence_threshold, 
    **env_kwargs, 
)

# Convert to VecEnv 
env_trade = DummyVecEnv([lambda: e_trade_gym])

# Get initial state using VecEnv API
state = env_trade.reset()

df_account_value_a2c, df_actions_a2c = DRLAgent.DRL_prediction(
    model=trained_a2c,
    environment=e_trade_gym  # <-- use e_trade_gym, not env_trade
)

# Save results
df_account_value_a2c.to_csv(
    "./" + RESULTS_DIR + "/df_account_value_a2c.csv"
)
df_actions_a2c.to_csv(
    "./" + RESULTS_DIR + "/df_actions_a2c.csv"
)

==============Start Trading A2C===========
hit end!


In [36]:
processed.to_csv("processed.csv")

In [40]:
print("==============Model Training===========")
model_ppo = agent.get_model("ppo")
trained_ppo = agent.train_model(
    model=model_ppo, tb_log_name="ppo", total_timesteps=timesteps_dict['ppo'])

==============Model Training===========
{'n_steps': 2048, 'ent_coef': 0.01, 'learning_rate': 0.00025, 'batch_size': 64}
Using cpu device
-----------------------------------
| time/              |            |
|    fps             | 86         |
|    iterations      | 1          |
|    time_elapsed    | 23         |
|    total_timesteps | 2048       |
| train/             |            |
|    reward          | 103.69364  |
|    reward_max      | 810.85016  |
|    reward_mean     | 5.5615244  |
|    reward_min      | -809.51605 |
-----------------------------------
----------------------------------------
| time/                   |            |
|    fps                  | 80         |
|    iterations           | 2          |
|    time_elapsed         | 50         |
|    total_timesteps      | 4096       |
| train/                  |            |
|    approx_kl            | 0.0174094  |
|    clip_fraction        | 0.219      |
|    clip_range           | 0.2        |
|    entropy_loss    

In [41]:
print("==============Start Trading PPO===========")
e_trade_gym = StockTradingEnv(
    df=trade, turbulence_threshold=turbulence_threshold, **env_kwargs)

df_account_value_ppo, df_actions_ppo = DRLAgent.DRL_prediction(
    model=trained_ppo, environment=e_trade_gym                          # Đổi model
)
df_account_value_ppo.to_csv(
    "./" + RESULTS_DIR + "/df_account_value_ppo.csv"
)
df_actions_ppo.to_csv("./" + RESULTS_DIR +
                    "/df_actions_ppo.csv")

==============Start Trading PPO===========
hit end!


In [47]:
df_summary = ensemble_agent.run_ensemble_strategy(A2C_model_kwargs,
                                                 PPO_model_kwargs,
                                                 DDPG_model_kwargs,
                                                SAC_model_kwargs,
                                                 TD3_model_kwargs,
                                                 timesteps_dict)

============Start Ensemble Strategy============
turbulence_threshold:  155.4156534549665
======Model training from:  2009-01-01 to  2015-10-01
======a2c Training========
{'n_steps': 5, 'ent_coef': 0.01, 'learning_rate': 0.0007}
Using cpu device
Logging to tensorboard_log/a2c\a2c_126_1
-------------------------------------
| time/                 |           |
|    fps                | 68        |
|    iterations         | 100       |
|    time_elapsed       | 7         |
|    total_timesteps    | 500       |
| train/                |           |
|    entropy_loss       | -41.2     |
|    explained_variance | -0.00378  |
|    learning_rate      | 0.0007    |
|    n_updates          | 99        |
|    policy_loss        | 2.16e+03  |
|    reward             | -41.88243 |
|    reward_max         | 211.82245 |
|    reward_mean        | 19.52525  |
|    reward_min         | -81.86726 |
|    std                | 1         |
|    value_loss         | 7.23e+03  |
------------------------------

In [48]:
df_summary


Iter   Val Start     Val End Model Used A2C Sharpe PPO Sharpe DDPG Sharpe  \
0    126  2015-10-01  2015-12-31        PPO   0.051078   0.091764        None   
1    189  2015-12-31  2016-04-04        A2C   0.083936  -0.084732        None   
2    252  2016-04-04  2016-07-01        A2C  -0.014955  -0.089989        None   
3    315  2016-07-01  2016-09-30        A2C  -0.013258  -0.256729        None   
4    378  2016-09-30  2016-12-30        A2C   0.353105   0.323751        None   
5    441  2016-12-30  2017-04-03        PPO   0.102553   0.120141        None   
6    504  2017-04-03  2017-07-03        PPO  -0.015282   0.055627        None   
7    567  2017-07-03  2017-10-02        PPO  -0.308336  -0.176114        None   
8    630  2017-10-02  2018-01-02        A2C   0.413492   0.376187        None   
9    693  2018-01-02  2018-04-04        PPO  -0.139885   -0.10427        None   
10   756  2018-04-04  2018-07-03        PPO   0.025627   0.169047        None   
11   819  2018-07-03  2018-10-02        PPO   0.276327   0.350816        None   
12   882  2018-10-02  2019-01-03        PPO  -0.199215  -0.168745        None   
13   945  2019-01-03  2019-04-04        PPO   0.292855    0.36244        None   
14  1008  2019-04-04  2019-07-05        A2C  -0.035598  -0.230028        None   
15  1071  2019-07-05  2019-10-03        A2C  -0.157522  -0.350254        None   
16  1134  2019-10-03  2020-01-03        PPO   0.358957   0.376717        None   

   SAC Sharpe TD3 Sharpe  
0        None       None  
1        None       None  
2        None       None  
3        None       None  
4        None       None  
5        None       None  
6        None       None  
7        None       None  
8        None       None  
9        None       None  
10       None       None  
11       None       None  
12       None       None  
13       None       None  
14       None       None  
15       None       None  
16       None       None

In [49]:
df_summary.to_csv('saved_result_us/sharpe.csv')

<a id='6'></a>
# Part 7: Backtest Our Strategy
Backtesting plays a key role in evaluating the performance of a trading strategy. Automated backtesting tool is preferred because it reduces the human error. We usually use the Quantopian pyfolio package to backtest our trading strategies. It is easy to use and consists of various individual plots that provide a comprehensive image of the performance of a trading strategy.

In [50]:
unique_trade_date = processed[(processed.date > TEST_START_DATE)&(processed.date <= TEST_END_DATE)].date.unique()
df_trade_date = pd.DataFrame({'datadate':unique_trade_date})

In [53]:

df_account_value = pd.DataFrame()
for i in range(rebalance_window + validation_window, len(unique_trade_date) + 1, rebalance_window):
    temp = pd.read_csv(f'results/account_value_trade_ensemble_{i}.csv')
    df_account_value = pd.concat([df_account_value, temp], ignore_index=True)

sharpe = (252 ** 0.5) * df_account_value.account_value.pct_change(1).mean() / df_account_value.account_value.pct_change(1).std()
print('Sharpe Ratio: ', sharpe)



Sharpe Ratio:  -0.1529718736709135


In [55]:
df_account_value.to_csv('saved_result_us/df_account_value.csv')

In [33]:
df_account_value_a2c = pd.read_csv('results/df_account_value_a2c.csv', index_col=0)
df_account_value_a2c

date  account_value
0     2016-01-04   1.000000e+08
1     2016-01-05   9.986752e+07
2     2016-01-06   9.821808e+07
3     2016-01-07   9.546393e+07
4     2016-01-08   9.428933e+07
...          ...            ...
1089  2020-05-01   9.589094e+07
1090  2020-05-04   9.633051e+07
1091  2020-05-05   9.709900e+07
1092  2020-05-06   9.641995e+07
1093  2020-05-07   9.793942e+07

[1094 rows x 2 columns]

In [42]:
df_account_value_ppo = pd.read_csv('results/df_account_value_ppo.csv', index_col=0)
df_account_value_ppo

date  account_value
0     2016-01-04   1.000000e+08
1     2016-01-05   9.999295e+07
2     2016-01-06   9.972108e+07
3     2016-01-07   9.890485e+07
4     2016-01-08   9.835471e+07
...          ...            ...
1089  2020-05-01   1.338189e+08
1090  2020-05-04   1.335776e+08
1091  2020-05-05   1.338158e+08
1092  2020-05-06   1.327825e+08
1093  2020-05-07   1.344637e+08

[1094 rows x 2 columns]